# Reccommendation System

### Scenario

You joined as the new memeber of a small start-up team. Together we are building a new app to sell cool 3rd party products! So far, the sales team worked tirelessly and managed to acquire over 50 merchants who each have different brands and products offerings. The developers have made a ton of progress on the mobile app and there's a bunch of user activity on the app. The analytics platform Mixpanel is used to collect all the user event data. The next step is to optimize user conversion rates by offering new recommendations based on the analytics data.

### Goal

Your task is to recommend a product that a user is most likely to buy next using the purchase history provided.

For the purpose of this interview test, we have provided mock data on customer purchase history from an e-commerce retail company. The 'Purchased Product' events were queried through Mixpanel's API and is exported into the file training_mixpanel.txt, as provided, in JSON format. Each event describes a singular product purchased by a particular user, with descriptive attributes of the product (e.g., quantity, unit price). Transactions purchasing multiple products is denoted by invoice_no.

### Methodology 

The pipeline first consisted of importing and exploring the data. This provided a vital intuition about the dataset and helped define the models and method of approaching this problem. The simplest and most robust model to go with is the user based collaborative filter recommender system. However, we can see that the data contains about 300 users or 10% of the population that have bought less than 5 unique items. This lends to a cold-start problem. Something that's taken care of by content-based recommendation systems. So, it was decided that the best method to tackle this task is by utilizing a **hybridized version of the collaborative filter and content based recommender systems** 

## 0. Import Libraries

In [109]:
import numpy as np
import pandas as pd
import scipy
import math
import random
import json
import nltk 
import sklearn

import matplotlib.pyplot as plt
%matplotlib inline

from nltk.corpus import stopwords
from sklearn.metrics import roc_auc_score
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from scipy.sparse.linalg import svds

## 1. Data Exploration

In [4]:
filename = "training_mixpanel.txt"

with open(filename) as f: 
    python_obj = json.load(f)
python_obj

[{'event': 'Purchased Product',
  'properties': {'invoice_no': '536365',
   'product_id': '85123A',
   'description': 'WHITE HANGING HEART T-LIGHT HOLDER',
   'quantity': 6,
   'invoice_date': '12/1/2010 8:26',
   'unit_price': 2.55,
   'customer_id': 17850,
   'country': 'United Kingdom'}},
 {'event': 'Purchased Product',
  'properties': {'invoice_no': '536365',
   'product_id': '71053',
   'description': 'WHITE METAL LANTERN',
   'quantity': 6,
   'invoice_date': '12/1/2010 8:26',
   'unit_price': 3.39,
   'customer_id': 17850,
   'country': 'United Kingdom'}},
 {'event': 'Purchased Product',
  'properties': {'invoice_no': '536365',
   'product_id': '22752',
   'description': 'SET 7 BABUSHKA NESTING BOXES',
   'quantity': 2,
   'invoice_date': '12/1/2010 8:26',
   'unit_price': 7.65,
   'customer_id': 17850,
   'country': 'United Kingdom'}},
 {'event': 'Purchased Product',
  'properties': {'invoice_no': '536365',
   'product_id': '21730',
   'description': 'GLASS STAR FROSTED T-LIGHT

So we can see that the data set is a collection of events, all of them are a product being purchased. The event has properties such as invoice number, product id, description, quantity, invoice date, unit price, customer id, and country. 

The customer id is our user. We can manipulate this data set in a variety of ways to gain some useful information on how best to approach this problem. 

How often was a product bought? 
How many different products did each user buy?
Where were most of the products bought from? 
what time of day were the products brought at?

All these may seem unrelated but can produce meaningful insights down the road. 

In [3]:
print (json.dumps(python_obj[0], sort_keys=True, indent=4)) #pretty printing

{
    "event": "Purchased Product",
    "properties": {
        "country": "United Kingdom",
        "customer_id": 17850,
        "description": "WHITE HANGING HEART T-LIGHT HOLDER",
        "invoice_date": "12/1/2010 8:26",
        "invoice_no": "536365",
        "product_id": "85123A",
        "quantity": 6,
        "unit_price": 2.55
    }
}


### We move over to pandas to visualize and manipulate our data

Since all the events are "purchased product" we can collect them separatel and work with just the properties

In [5]:
properties = []
for i in range(len(python_obj)):
    properties.append(python_obj[i].get('properties'))

In [84]:
prop = pd.DataFrame(properties)  #Creating a DataFrame for our data
prop

country  customer_id                          description  \
0       United Kingdom        17850   WHITE HANGING HEART T-LIGHT HOLDER   
1       United Kingdom        17850                  WHITE METAL LANTERN   
2       United Kingdom        17850         SET 7 BABUSHKA NESTING BOXES   
3       United Kingdom        17850    GLASS STAR FROSTED T-LIGHT HOLDER   
4       United Kingdom        17850               HAND WARMER UNION JACK   
5       United Kingdom        17850            HAND WARMER RED POLKA DOT   
6       United Kingdom        13047        ASSORTED COLOUR BIRD ORNAMENT   
7       United Kingdom        13047           POPPY'S PLAYHOUSE BEDROOM    
8       United Kingdom        13047            POPPY'S PLAYHOUSE KITCHEN   
9       United Kingdom        13047    FELTCRAFT PRINCESS CHARLOTTE DOLL   
10      United Kingdom        13047              IVORY KNITTED MUG COSY    
11      United Kingdom        13047   BOX OF 6 ASSORTED COLOUR TEASPOONS   
12      United Kingdom        13047        BOX OF VINTAGE JIGSAW BLOCKS    
13      United Kingdom        13047             HOME BUILDING BLOCK WORD   
14      United Kingdom        13047             LOVE BUILDING BLOCK WORD   
15      United Kingdom        13047          RECIPE BOX WITH METAL HEART   
16      United Kingdom        13047             JAM MAKING SET WITH JARS   
17      United Kingdom        13047          RED COAT RACK PARIS FASHION   
18      United Kingdom        13047         BLUE COAT RACK PARIS FASHION   
19      United Kingdom        13047             BATH BUILDING BLOCK WORD   
20              France        12583            ALARM CLOCK BAKELIKE PINK   
21              France        12583            ALARM CLOCK BAKELIKE RED    
22              France        12583           ALARM CLOCK BAKELIKE GREEN   
23              France        12583      PANDA AND BUNNIES STICKER SHEET   
24              France        12583                     STARS GIFT TAPE    
25              France        12583          INFLATABLE POLITICAL GLOBE    
26              France        12583   VINTAGE HEADS AND TAILS CARD GAME    
27              France        12583      SET/2 RED RETROSPOT TEA TOWELS    
28              France        12583  ROUND SNACK BOXES SET OF4 WOODLAND    
29              France        12583                  SPACEBOY LUNCH BOX    
...                ...          ...                                  ...   
322845  United Kingdom        15804      VICTORIAN GLASS HANGING T-LIGHT   
322846  United Kingdom        15804       EMBOSSED GLASS TEALIGHT HOLDER   
322847  United Kingdom        15804     ZINC WILLIE WINKIE  CANDLE STICK   
322848  United Kingdom        15804                   RABBIT NIGHT LIGHT   
322849  United Kingdom        15804        ASSORTED COLOUR BIRD ORNAMENT   
322850  United Kingdom        15804   MULTI COLOUR SILVER T-LIGHT HOLDER   
322851  United Kingdom        15804           ALARM CLOCK BAKELIKE GREEN   
322852  United Kingdom        15804          LARGE CHINESE STYLE SCISSOR   
322853  United Kingdom        15804      SET 12 RETRO WHITE CHALK STICKS   
322854  United Kingdom        15804          BOX OF 24 COCKTAIL PARASOLS   
322855  United Kingdom        15804         ANTIQUE SILVER T-LIGHT GLASS   
322856  United Kingdom        15804     SMALL MEDINA STAMPED METAL BOWL    
322857  United Kingdom        15804           MAGNETS PACK OF 4 SWALLOWS   
322858  United Kingdom        15804       ZINC T-LIGHT HOLDER STAR LARGE   
322859  United Kingdom        15804       FAIRY TALE COTTAGE NIGHT LIGHT   
322860  United Kingdom        13113     SET OF 3 HANGING OWLS OLLIE BEAK   
322861  United Kingdom        13113        RED RETROSPOT ROUND CAKE TINS   
322862          France        12680             CIRCUS PARADE LUNCH BOX    
322863          France        12680       PLASTERS IN TIN CIRCUS PARADE    
322864          France        12680            PLASTERS IN TIN STRONGMAN   
322865          France        12680            ALARM CLOCK BAKE

In [85]:
print(len(pd.value_counts(prop["customer_id"])))

4363


In [86]:
print(len(pd.value_counts(prop["product_id"])))

3677


4636 unique users and 3677 unique products

In [87]:
prop.describe()

customer_id       quantity     unit_price
count  322875.000000  322875.000000  322875.000000
mean    15285.738180      12.103250       2.934132
std      1712.664883     278.315144       6.228682
min     12346.000000  -80995.000000       0.000000
25%     13952.000000       2.000000       1.250000
50%     15150.000000       5.000000       1.950000
75%     16788.000000      12.000000       3.750000
max     18287.000000   80995.000000    1100.440000

highest number of purchases is 8000 and so is the highest number of returns. Smells fishy! Was it the same user? Was it the same product? Should we remove them as an outlier?

In [88]:
product_purchases = prop.groupby(['product_id'])['quantity'].sum().sort_values(ascending = False).reset_index()
product_purchases #absolute times products been purchased

product_id  quantity
0         22197     43331
1         84077     35442
2        85099B     33126
3         84879     29418
4         21212     28255
5         23084     25074
6        85123A     24776
7         22616     23368
8         21977     22297
9         17003     22005
10        15036     20532
11        21915     19252
12        22492     17976
13        22178     17929
14        84991     15505
15        23203     15071
16        20725     14627
17        22469     14566
18        22386     13549
19        22693     13468
20        84826     13412
21        16014     13227
22        84755     12757
23        21213     12731
24        47566     12468
25        22961     12123
26       85099F     11782
27        71459     11746
28        84946     11603
29        22086     11553
...         ...       ...
3647      90168         0
3648     90177A         0
3649      21667         0
3650     85023C        -1
3651      85068        -1
3652      85065        -1
3653      20957        -1
3654      35832        -1
3655      85126        -1
3656     85098B        -1
3657      37503        -1
3658     84856S        -1
3659     90185C        -1
3660      79320        -1
3661      84839        -1
3662      72815        -2
3663     84750A        -3
3664      85063        -3
3665      85042        -3
3666     79323P        -4
3667      22769        -4
3668      35400        -6
3669      21412        -6
3670      20703        -6
3671     79323W        -8
3672      22034        -9
3673      21144       -12
3674       CRUK       -16
3675      21645       -24
3676      84347     -3401

[3677 rows x 2 columns]

In [89]:
user_purchases = prop.groupby(['customer_id'])['quantity'].sum().sort_values(ascending = False).reset_index()
user_purchases #absolute times user has purchased products  i. purchases - returns

customer_id  quantity
0           14646    150505
1           12415     61126
2           14911     60548
3           17450     49962
4           14298     46744
5           13694     46370
6           18102     45750
7           17511     44934
8           14156     43254
9           16684     38061
10          16333     31008
11          15311     29784
12          16422     29579
13          17404     27043
14          16029     26891
15          13089     23456
16          15769     22360
17          15061     21718
18          12931     20443
19          12748     19349
20          17949     19241
21          13798     18312
22          17381     17878
23          17841     17815
24          13081     15060
25          12901     14756
26          13098     14198
27          13027     14160
28          17857     13852
29          13408     13167
...           ...       ...
4333        16428        -1
4334        12943        -1
4335        14679        -1
4336        16995        -1
4337        16138        -1
4338        16061        -1
4339        14119        -2
4340        12870        -2
4341        17547        -4
4342        12605        -4
4343        14627        -5
4344        17820        -5
4345        16262        -5
4346        13693        -6
4347        14777        -9
4348        16579       -12
4349        13829       -12
4350        18141       -12
4351        13958       -23
4352        15728       -34
4353        15638       -52
4354        12666       -56
4355        18256       -70
4356        17548      -132
4357        17307      -144
4358        16252      -158
4359        16742      -190
4360        14213      -244
4361        15823      -282
4362        16546      -303

[4363 rows x 2 columns]

Let's just keep it simple for now and look at solely the purchases for our recommendations. If they bought it in the first place they must have been looking for something similar. 

In [90]:
user_purchases = prop.groupby(['customer_id', 'quantity']).size().sort_values(ascending = True).reset_index()
user_purchases #absolute times user has purchased products  i. purchases - returns

customer_id  quantity     0
0            12346    -74215     1
1            14722         3     1
2            17481         1     1
3            14720        24     1
4            14720        16     1
5            14719        16     1
6            14719        10     1
7            14719         9     1
8            14722         4     1
9            17481        10     1
10           17481        18     1
11           17481        48     1
12           17481        72     1
13           14719        -1     1
14           14716       120     1
15           14716        24     1
16           14716        18     1
17           17481        16     1
18           14722        23     1
19           17481        -1     1
20           14723         9     1
21           14729         6     1
22           14729         5     1
23           14729         4     1
24           14727         6     1
25           14727         4     1
26           14725       120     1
27           14725        56     1
28           14725        36     1
29           14725        30     1
...            ...       ...   ...
43126        15005         2   306
43127        16241         1   310
43128        14606         2   333
43129        16904         1   351
43130        18283         1   354
43131        14298        24   354
43132        15039         1   357
43133        16549         1   360
43134        14096         3   379
43135        17841         3   400
43136        14456         1   430
43137        14911         4   431
43138        14527         1   442
43139        14911         2   442
43140        13263         2   456
43141        14911        24   460
43142        15311         2   482
43143        15311         1   503
43144        13263         1   505
43145        13089        12   511
43146        18118         1   638
43147        12748         2   706
43148        14911         6   710
43149        14096         2   736
43150        17841         2  1206
43151        14911        12  1270
43152        14606         1  1441
43153        14096         1  1842
43154        12748         1  1864
43155        17841         1  3368

[43156 rows x 3 columns]

User 12346 has bought and returned 74 thousand items..

## 2. Data Preprocessing

Let's just keep it simple for now and look at solely the purchases for our recommendations. If they bought it in the first place they must have been looking for something similar. 

In [91]:
prop = prop[prop['quantity']>0] #removes negative values i.e. returns
prop.head()

country  customer_id                         description  \
0  United Kingdom        17850  WHITE HANGING HEART T-LIGHT HOLDER   
1  United Kingdom        17850                 WHITE METAL LANTERN   
2  United Kingdom        17850        SET 7 BABUSHKA NESTING BOXES   
3  United Kingdom        17850   GLASS STAR FROSTED T-LIGHT HOLDER   
4  United Kingdom        17850              HAND WARMER UNION JACK   

     invoice_date invoice_no product_id  quantity  unit_price  
0  12/1/2010 8:26     536365     85123A         6        2.55  
1  12/1/2010 8:26     536365      71053         6        3.39  
2  12/1/2010 8:26     536365      22752         2        7.65  
3  12/1/2010 8:26     536365      21730         6        4.25  
4  12/1/2010 8:28     536366      22633         6        1.85

In [92]:
print(len(pd.value_counts(prop["customer_id"])))

4335


In [93]:
print(len(pd.value_counts(prop["product_id"])))

3659


 Let's give a weight to these purchases by multiplying the quantity with unit price to get a weighted strength score. We might want to give good recommendations of most products bought but we also want to increase our revenue! 

In [94]:
value = prop.quantity * prop.unit_price
#Scale our results with log so the data set isn't skewewd by a few large purchases
value_scaled = np.log2(1+value)  ## add one so that values below 1 don't push us back negative and zero values don't put as -inf
prop['value'] = value_scaled
#prop['quantityScaled'] = np.log(prop.quantity) #Perhaps nominal quantity is a better measure without economics playing a part
prop

C:\Users\Prakash14\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.


country  customer_id                          description  \
0       United Kingdom        17850   WHITE HANGING HEART T-LIGHT HOLDER   
1       United Kingdom        17850                  WHITE METAL LANTERN   
2       United Kingdom        17850         SET 7 BABUSHKA NESTING BOXES   
3       United Kingdom        17850    GLASS STAR FROSTED T-LIGHT HOLDER   
4       United Kingdom        17850               HAND WARMER UNION JACK   
5       United Kingdom        17850            HAND WARMER RED POLKA DOT   
6       United Kingdom        13047        ASSORTED COLOUR BIRD ORNAMENT   
7       United Kingdom        13047           POPPY'S PLAYHOUSE BEDROOM    
8       United Kingdom        13047            POPPY'S PLAYHOUSE KITCHEN   
9       United Kingdom        13047    FELTCRAFT PRINCESS CHARLOTTE DOLL   
10      United Kingdom        13047              IVORY KNITTED MUG COSY    
11      United Kingdom        13047   BOX OF 6 ASSORTED COLOUR TEASPOONS   
12      United Kingdom        13047        BOX OF VINTAGE JIGSAW BLOCKS    
13      United Kingdom        13047             HOME BUILDING BLOCK WORD   
14      United Kingdom        13047             LOVE BUILDING BLOCK WORD   
15      United Kingdom        13047          RECIPE BOX WITH METAL HEART   
16      United Kingdom        13047             JAM MAKING SET WITH JARS   
17      United Kingdom        13047          RED COAT RACK PARIS FASHION   
18      United Kingdom        13047         BLUE COAT RACK PARIS FASHION   
19      United Kingdom        13047             BATH BUILDING BLOCK WORD   
20              France        12583            ALARM CLOCK BAKELIKE PINK   
21              France        12583            ALARM CLOCK BAKELIKE RED    
22              France        12583           ALARM CLOCK BAKELIKE GREEN   
23              France        12583      PANDA AND BUNNIES STICKER SHEET   
24              France        12583                     STARS GIFT TAPE    
25              France        12583          INFLATABLE POLITICAL GLOBE    
26              France        12583   VINTAGE HEADS AND TAILS CARD GAME    
27              France        12583      SET/2 RED RETROSPOT TEA TOWELS    
28              France        12583  ROUND SNACK BOXES SET OF4 WOODLAND    
29              France        12583                  SPACEBOY LUNCH BOX    
...                ...          ...                                  ...   
322845  United Kingdom        15804      VICTORIAN GLASS HANGING T-LIGHT   
322846  United Kingdom        15804       EMBOSSED GLASS TEALIGHT HOLDER   
322847  United Kingdom        15804     ZINC WILLIE WINKIE  CANDLE STICK   
322848  United Kingdom        15804                   RABBIT NIGHT LIGHT   
322849  United Kingdom        15804        ASSORTED COLOUR BIRD ORNAMENT   
322850  United Kingdom        15804   MULTI COLOUR SILVER T-LIGHT HOLDER   
322851  United Kingdom        15804           ALARM CLOCK BAKELIKE GREEN   
322852  United Kingdom        15804          LARGE CHINESE STYLE SCISSOR   
322853  United Kingdom        15804      SET 12 RETRO WHITE CHALK STICKS   
322854  United Kingdom        15804          BOX OF 24 COCKTAIL PARASOLS   
322855  United Kingdom        15804         ANTIQUE SILVER T-LIGHT GLASS   
322856  United Kingdom        15804     SMALL MEDINA STAMPED METAL BOWL    
322857  United Kingdom        15804           MAGNETS PACK OF 4 SWALLOWS   
322858  United Kingdom        15804       ZINC T-LIGHT HOLDER STAR LARGE   
322859  United Kingdom        15804       FAIRY TALE COTTAGE NIGHT LIGHT   
322860  United Kingdom        13113     SET OF 3 HANGING OWLS OLLIE BEAK   
322861  United Kingdom        13113        RED RETROSPOT ROUND CAKE TINS   
322862          France        12680             CIRCUS PARADE LUNCH BOX    
322863          France        12680       PLASTERS IN TIN CIRCUS PARADE    
322864          France        12680            PLASTERS IN TIN STRONGMAN   
322865          France        12680            ALARM CLOCK BAKE

In [95]:
prop = prop.drop_duplicates() #let's drop duplicate rows
prop.describe()

customer_id       quantity     unit_price          value
count  311884.000000  311884.000000  311884.000000  311884.000000
mean    15286.186287      13.297729       2.881865       3.555415
std      1712.707014     202.647578       4.419935       1.458827
min     12346.000000       1.000000       0.000000       0.000000
25%     13952.000000       2.000000       1.250000       2.572890
50%     15150.000000       6.000000       1.950000       3.689299
75%     16790.000000      12.000000       3.750000       4.378512
max     18287.000000   80995.000000     649.500000      17.362137

There were probably a few interactions that were only returns. This DF doesn't contain that.

In [98]:
Purchases_df = prop.groupby(['customer_id', 'product_id'])['value'].mean().reset_index()
print('# of unique customer/item purchases: %d' % len(Purchases_df))
Purchases_df.head(10)


# of unique customer/item purchases: 212995


customer_id product_id      value
0        12346      23166  16.236025
1        12347      16008   2.807355
2        12347      17021   3.560715
3        12347      20665   4.224966
4        12347      20719   3.247928
5        12347      20780   5.827819
6        12347      20782   5.084915
7        12347      20966   3.754888
8        12347      21035   4.224966
9        12347      21041   4.224966

In [99]:
Purchases_df.describe()

customer_id          value
count  212995.000000  212995.000000
mean    15273.910899       3.490932
std      1710.864276       1.345601
min     12346.000000       0.000000
25%     13862.000000       2.572890
50%     15214.000000       3.666757
75%     16771.000000       4.238515
max     18287.000000      17.362137

## 2. Data Pre-processing

First thing to always do in the ML preprocessing pipeline is to split the dataset. 

If this step is done later on, we would have applied our model over the whole dataset and fit really well on it and would be testing ourselves again on the evaluated data. Like asking darth vader if hes evil and he says no hes not evil so we believe him. 

In [ ]:
y = Purchases_df['customer_id']
y.iloc[:].value_counts()

In [ ]:

training_purchases, testing_purchases = train_test_split(Purchases_df, stratify=y.iloc[:], test_size=0.2)
                                                           
                                                             

print('# of training purchases: %d' % len(training_purchases))
print('# of testing purchases: %d' % len(testing_purchases))

In [ ]:
print(len(pd.value_counts(training_purchases["customer_id"])))

In [ ]:
training_purchases, testing_purchases = train_test_split(prop, test_size = 0.2)  

print('# of training purchases: %d' % len(training_purchases))
print('# of testing purchases: %d' % len(testing_purchases))

In [ ]:
print(len(pd.value_counts(testing_purchases["customer_id"])))

In [100]:
#Indexing by personId to speed up the searches during evaluation
purchases_full_indexed_df = Purchases_df.set_index('customer_id')
#training_indexed_df = training_purchases.set_index('customer_id')
#testing_indexed_df = testing_purchases.set_index('customer_id')

In [101]:
purchases_full_indexed_df

product_id      value
customer_id                      
12346            23166  16.236025
12347            16008   2.807355
12347            17021   3.560715
12347            20665   4.224966
12347            20719   3.247928
12347            20780   5.827819
12347            20782   5.084915
12347            20966   3.754888
12347            21035   4.224966
12347            21041   4.224966
12347            21064   5.075952
12347            21154   3.754888
12347            21171   4.201634
12347            21265   4.608809
12347            21578   3.857981
12347            21636   3.321928
12347            21731   4.571491
12347            21791   4.318065
12347            21832   4.378512
12347            21975   3.827819
12347            21976   3.827819
12347            22131   3.666757
12347            22134   2.594549
12347            22195   4.700144
12347            22196   3.952483
12347            22212   3.765535
12347            22252   4.000000
12347            22371   5.006357
12347            22372   4.169925
12347            22374   4.489711
...                ...        ...
18287            22603   4.419539
18287            22644   4.201634
18287            22752   5.129283
18287            22753   3.485427
18287            22754   3.485427
18287            22755   3.485427
18287            22756   4.000000
18287            22758   4.000000
18287            22807   4.224966
18287            22865   4.711495
18287            22866   4.711495
18287            23076   4.954196
18287            23078   4.954196
18287            23223   5.351911
18287            23264   4.761781
18287            23267   4.954196
18287            23269   5.733354
18287            23272   4.378512
18287            23376   4.301588
18287            23378   3.372952
18287            23445   4.137504
18287            35967   3.875780
18287            47422   3.469886
18287           72349B   5.535578
18287           72351A   5.683696
18287           84507C   4.026800
18287            84584   4.026800
18287            84920   4.000000
18287           85039A   6.141596
18287           85040A   5.147494

[212995 rows x 2 columns]

## 3. Content Based Filtering

In [102]:
print(len(pd.value_counts(prop["product_id"])))

3659


In [103]:
print(len(pd.value_counts(prop["description"])))

3860


There seems to be 3659 unique product ids, but 3860 unique product descriptions. 

So there must be a product id with two different descriptions. We'll just focus on our product ids and discard the extra discriptions.

In [104]:
collab_df = prop.drop_duplicates('product_id')
len(collab_df)
collab_df.head()

country  customer_id                         description  \
0  United Kingdom        17850  WHITE HANGING HEART T-LIGHT HOLDER   
1  United Kingdom        17850                 WHITE METAL LANTERN   
2  United Kingdom        17850        SET 7 BABUSHKA NESTING BOXES   
3  United Kingdom        17850   GLASS STAR FROSTED T-LIGHT HOLDER   
4  United Kingdom        17850              HAND WARMER UNION JACK   

     invoice_date invoice_no product_id  quantity  unit_price     value  
0  12/1/2010 8:26     536365     85123A         6        2.55  4.026800  
1  12/1/2010 8:26     536365      71053         6        3.39  4.415488  
2  12/1/2010 8:26     536365      22752         2        7.65  4.026800  
3  12/1/2010 8:26     536365      21730         6        4.25  4.727920  
4  12/1/2010 8:28     536366      22633         6        1.85  3.596935

In [105]:
from sklearn.metrics.pairwise import linear_kernel
#color = (['WHITE', 'BLACK', 'BLUE', "RED", 'GREEN', 'YELLOW', 'ORANGE', 'PURPLE', 'INDIGO'])
stopwords_list = stopwords.words('english') 

vectorizer = TfidfVectorizer(analyzer = 'word',
                           ngram_range=(1,2),
                           min_df=0.0003,
                           max_df=0.5,
                           max_features = None,
                           lowercase=True,
                           stop_words=stopwords_list)
item_ids = prop['product_id'].drop_duplicates().tolist()
tfidf_matrix = vectorizer.fit_transform(collab_df['description'])
tfidf_feature_names = vectorizer.get_feature_names()
#cosine_similarities = linear_kernel(tfidf_matrix, tfidf_matrix)
tfidf_matrix

<3659x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 21055 stored elements in Compressed Sparse Row format>

Let's have a look at our features:

In [106]:
tfidf_feature_names

['10',
 '12',
 '12 blue',
 '12 colour',
 '12 coloured',
 '12 kids',
 '12 mini',
 '12 pencils',
 '12 pink',
 '12 red',
 '12 vintage',
 '120cm',
 '15',
 '15cm',
 '16',
 '16 vintage',
 '20',
 '20 dolly',
 '20 napkins',
 '200',
 '20light',
 '24',
 '30cm',
 '36',
 '36 colour',
 '36 doilies',
 '36 foil',
 '36 pencils',
 '3d',
 '3d sheet',
 '40',
 '40 cones',
 '42',
 '42 neckl',
 '45cm',
 '50',
 '50 christmas',
 '50 pieces',
 '60',
 '60 cake',
 '60cm',
 '70',
 '70 tray',
 '72',
 '72 retrospot',
 '72 skull',
 '75',
 '75 green',
 'a4',
 'a4 wall',
 'a6',
 'a6 size',
 'a7',
 'a7 size',
 'abstract',
 'abstract circles',
 'acapulco',
 'acapulco mat',
 'acrylic',
 'acrylic edwardian',
 'acrylic faceted',
 'acrylic hanging',
 'acrylic jewel',
 'advent',
 'advent calendar',
 'aid',
 'aid tin',
 'airline',
 'airline bag',
 'alarm',
 'alarm clock',
 'album',
 'alphabet',
 'alphabet design',
 'alphabet iron',
 'amber',
 'amber chunky',
 'amber drop',
 'amber glass',
 'amethyst',
 'anemone',
 'anemone ar

Now, to model the user profile, we take all the item profiles the user has bought and average them. 

In [107]:
def get_item_profile(item_id):
    """Obtains a vector profiling an item"""
    print(item_id)
    idx = item_ids.index(item_id)
    #print(idx)
    item_profile = tfidf_matrix[idx:idx+1] #The 1000 element row vector for the item
    return item_profile

def get_item_profiles(ids):
    """Get all the item profiles for a given list of items"""
    if type(ids)==str:
        print (len(ids))
        ids = [ids] #if isinstance(ids, list) else [ids] #to make sure we are always dealing with lists, even when a single element
    
    print(len(ids))
    item_profiles_list = [get_item_profile(x) for x in ids] #get all the items
        
    item_profiles = scipy.sparse.vstack(item_profiles_list) #stack them on top of each other
    return item_profiles

def build_users_profile(customer_id, purchases_full_indexed_df): 
    """Get all the"""
    purchases_customer_df = purchases_full_indexed_df.loc[customer_id] #Receive the customer id and log all their purchases
    user_item_profiles = get_item_profiles(purchases_customer_df['product_id'])
    user_profile_norm = sklearn.preprocessing.normalize(user_item_profiles)
    #print(user_item_profiles)
    return user_item_profiles

def build_users_profiles():
    #purchases_full_indexed_df = Purchases_df.set_index('customer_id')
    user_profiles = {}
    for user_id in purchases_full_indexed_df.index.unique():
        user_profiles[user_id] = build_users_profile(user_id,purchases_full_indexed_df)
        
    return user_profiles

In [110]:
user_profiles = build_users_profiles()
#user_profiles

5
1
23166
103
16008
17021
20665
20719
20780
20782
20966
21035
21041
21064
21154
21171
21265
21578
21636
21731
21791
21832
21975
21976
22131
22134
22195
22196
22212
22252
22371
22372
22374
22375
22376
22417
22422
22423
22432
22492
22494
22497
22550
22561
22621
22697
22698
22699
22725
22726
22727
22728
22729
22771
22772
22773
22774
22775
22805
22821
22945
22992
23076
23084
23146
23147
23162
23170
23171
23172
23173
23174
23175
23177
23271
23297
23308
23316
23420
23421
23422
23480
23497
23503
23506
23508
23552
47559B
47567B
47580
51014C
71477
84558A
84559A
84559B
84625A
84625C
84969
84991
84992
84997B
84997C
84997D
85116
85167B
85178
85232D
20
21211
21213
21725
21726
21967
21977
21980
21981
21982
21983
21985
22437
22616
22951
22952
23076
23077
23078
84988
84991
72
20685
20914
21086
21136
21231
21232
21411
21531
21533
21535
21563
21564
21787
22059
22064
22070
22071
22131
22195
22326
22333
22423
22430
22441
22553
22554
22555
22556
22557
22567
22601
22666
22692
22704
22720
22722
22832
22960
2

84912A
84987
84988
84997B
84997D
85014A
85048
85049G
85227
32
20665
20674
20676
20725
20728
20750
21080
21212
21246
21424
21426
22302
22303
22326
22328
22352
22383
22384
22551
22554
22555
22619
22631
22659
22740
23199
23204
23206
23208
23236
84997B
85099B
62
20685
20712
20713
20719
20723
20724
20725
20728
21121
21212
21429
21439
21463
21464
21578
21621
21648
21731
21883
21931
21936
21937
21976
22299
22326
22328
22329
22355
22362
22363
22379
22380
22381
22382
22383
22384
22386
22398
22399
22435
22467
22504
22759
22960
23156
23191
23201
23204
23236
23237
23240
23256
23310
23369
47590A
47590B
70006
84997A
84997B
84997C
84997D
85099B
62
16169E
21115
21251
21314
21340
21481
21791
21912
21976
22139
22179
22417
22418
22423
22466
22492
22535
22596
22621
22629
22630
22634
22635
22666
22720
22723
22807
22894
22895
22932
22937
22938
22941
22952
22955
22964
22965
22966
22979
22982
22993
23048
23108
23163
23198
23199
23215
23243
23293
23297
23308
23319
23345
23346
23480
35471D
47566
84347
84356
848

24
20749
20750
22055
22061
22066
22128
22129
22138
22197
22446
22448
22500
22509
22649
22720
22721
22890
23244
23247
37446
37449
85203
85204
85232D
27
21108
21314
21519
21520
21733
21907
21933
22026
22066
22307
22646
22806
22893
22983
23234
23267
23311
23382
35922
37446
37495
47567B
72741
84535B
84796A
84991
85206A
31
20712
20713
20717
20728
21391
21481
21693
21694
21723
21936
21937
21944
22147
22271
22273
22384
22469
22503
22749
22961
22962
23199
23200
23202
23208
23209
23267
23321
23344
35810A
85099C
83
15039
20718
20719
20723
20724
20725
20981
21108
21135
21156
21238
21680
21705
21731
21746
21749
21980
21981
21990
22037
22098
22151
22232
22248
22252
22302
22303
22319
22328
22329
22352
22356
22367
22385
22390
22396
22399
22419
22420
22554
22628
22629
22632
22661
22720
22742
22859
22893
22907
22915
22957
22962
22967
22968
22969
22994
23004
23008
23065
23066
23078
23199
23204
23254
23281
35923
71459
79190A
79190B
79191B
84596B
84596F
84879
84945
85014B
85040A
85099B
85169A
85169D
85170

22526
22605
22619
22620
22625
22666
22727
22960
23081
23169
23201
23203
23205
23209
23240
23245
23284
23298
23348
23395
23407
23469
47566
47590B
47591D
48138
84375
85066
85099B
19
20674
20676
20712
20749
20750
21238
21242
21245
21531
21533
21535
22303
22326
22551
22556
22628
22631
22659
85099B
16
21084
21090
21155
21212
21558
22367
22402
22471
22553
22557
22585
22630
22899
46000M
48184
85019B
101
18007
20665
20724
20725
20749
20750
20764
20766
20770
20914
20979
21165
21216
21218
21285
21559
21731
21770
21787
21791
21844
21889
21906
21908
21912
21914
21915
21935
22027
22029
22070
22071
22090
22117
22174
22191
22192
22193
22326
22328
22329
22355
22375
22376
22382
22413
22471
22472
22474
22494
22548
22549
22551
22554
22555
22624
22625
22626
22627
22630
22631
22635
22712
22715
22725
22726
22727
22728
22729
22753
22754
22755
22757
22758
22759
22815
22816
23159
23177
23202
23229
23234
23238
23240
23241
23242
23244
23245
23247
23275
23371
23372
23493
23497
23570
37467
79066K
79191C
84086C
846

22551
22554
22555
22556
22564
22568
22569
22570
22571
22572
22574
22577
22580
22613
22622
22629
22631
22634
22636
22637
22661
22668
22669
22711
22716
22721
22733
22749
22750
22751
22779
22780
22814
22815
22817
22824
22859
22865
22907
22940
22957
22964
22972
22992
23007
23010
23076
23079
23084
23108
23170
23177
23191
23194
23196
23204
23205
23206
23207
23211
23212
23232
23235
23236
23237
23239
23240
23243
23244
23245
23254
23255
23256
23264
23275
23280
23290
23292
23293
23307
23318
23346
23354
23389
23392
23433
23480
23506
23510
23545
23549
23559
23569
23570
23571
35910A
35910B
47518F
84251G
84536A
84997B
84997C
85015
85185B
85199L
85199S
85203
23
16045
20682
20712
20750
20766
20973
20975
21429
21452
21746
21891
22029
22138
22179
22331
22555
22620
23040
23126
23310
23388
23389
23506
141
20750
20752
20963
20978
20979
20984
21080
21086
21116
21137
21220
21293
21340
21394
21395
21411
21484
21494
21507
21509
21621
21658
21718
21791
21990
21993
22037
22077
22078
22080
22139
22173
22191
22280

...

23439
23503
23504
23505
23553
23555
35004C
35598B
72760B
82482
84050
84378
84380
85038
85053
85066
85184C
85231B
6
1
85099B
20
20668
20749
20750
21310
21455
21531
22086
22139
22487
22571
22583
22584
22601
22731
22809
22810
22950
23266
23275
35970
3
22222
22726
47566
110
10120
16012
16216
16218
16237
16238
16258A
17003
20619
20657
20668
20676
20956
21055
21080
21094
21212
21238
21245
21452
21484
21506
21559
21621
21703
21704
21791
21828
21914
21915
21917
21918
21987
21988
21990
21991
22037
22078
22080
22111
22142
22144
22150
22197
22208
22209
22211
22328
22448
22449
22454
22566
22595
22596
22610
22632
22636
22695
22718
22745
22746
22865
22867
22895
22908
22910
22940
22983
22992
23084
23127
23176
23177
23191
23193
23194
23215
23256
23287
23288
23308
23309
23318
23320
23329
23330
23351
23354
23365
23368
23369
23393
23394
23396
23500
23505
23507
23514
23569
23570
23571
84031B
84077
84509C
84510C
84596B
84596F
84992
85099B
85227
15
21164
21204
21380
21455
21621
21746
21749
21850
22120
22231

21894
21928
21992
22082
22091
22092
22098
22197
22339
22583
22720
23036
23294
23295
23296
71459
72140E
84836
85039B
85169A
85231B
22
15036
21479
21481
21484
22112
22113
22114
22182
22697
22698
23170
23171
23173
23174
23175
23245
75049L
79000
84029E
84029G
84030E
85048
27
21326
21494
21868
22141
22142
22158
22228
22233
22246
22247
22248
22251
22285
22301
22302
22303
22558
22584
22652
22809
22810
22960
22970
23210
23211
84945
85111
30
15034
15036
15039
21164
21165
21166
21175
21181
21231
21523
21524
21871
21874
21877
22030
22086
22611
22624
23077
23203
23349
23350
82482
82494L
82578
82580
84029G
84030E
85099B
85152
16
20967
20969
20970
20971
20972
21899
21901
21902
22149
22360
22364
22492
22566
22586
22587
22905
126
10080
15034
15056P
16216
16225
16237
17136A
20682
20971
20972
20982
20984
20996
21014
21034
21098
21158
21159
21162
21175
21181
21311
21326
21340
21358
21367
21368
21591
21592
21622
21703
21820
21829
21849
21850
21851
21915
21931
22086
22091
22112
22114
22139
22158
22162
2218

23298
23306
23318
23319
23320
23344
47503A
47504H
48187
84375
85099B
21
15056N
21260
21314
21407
21485
22413
22666
22722
22759
22794
22829
22844
22946
23053
23245
47566
48138
48187
72817
85099B
85123A
139
16161P
20725
20726
20727
20971
20977
20981
20982
20983
21080
21156
21212
21213
21327
21328
21504
21533
21535
21733
21888
21915
21918
21930
21977
21980
21986
22023
22026
22029
22030
22043
22045
22048
22064
22065
22138
22197
22271
22273
22274
22300
22301
22329
22348
22367
22382
22384
22385
22386
22405
22417
22503
22549
22551
22553
22554
22600
22602
22614
22621
22629
22637
22662
22663
22666
22667
22717
22718
22720
22722
22727
22730
22750
22751
22816
22818
22840
22841
22899
22907
22951
22960
22961
22966
22969
22972
22974
22984
22994
22996
23000
23006
23077
23126
23127
23203
23209
23231
23232
23236
23240
23266
23270
23281
23289
23290
23291
23292
23307
23319
23345
23346
23351
23366
23367
23368
23378
23380
23493
23494
23497
23502
23503
23506
23507
23508
23551
23552
23559
23582
23598
23691
23

84836
84947
84970L
85017B
85032D
47
21136
21232
21984
21986
22059
22189
22423
22425
22429
22457
22470
22624
22625
22697
22698
22699
22720
22722
22771
22772
22773
22776
22794
22795
22796
22799
22805
22847
22933
22934
22960
22961
22967
22969
22980
23050
23053
23160
23161
23163
23168
47566
72741
84755
84879
84946
85062
15
20793
21257
21377
21378
21379
21380
21755
21770
22092
22120
22169
22912
22913
22914
84637
133
16156S
16161U
20685
20751
20971
20972
20974
20977
20978
21098
21121
21122
21158
21159
21161
21165
21174
21175
21263
21380
21381
21479
21494
21495
21497
21499
21524
21563
21588
21621
21714
21746
21872
21899
21901
21907
21914
21915
21975
22074
22078
22084
22085
22086
22114
22117
22144
22150
22185
22273
22311
22423
22441
22468
22469
22470
22478
22479
22489
22491
22530
22533
22534
22536
22551
22553
22554
22555
22558
22561
22569
22629
22632
22633
22646
22666
22689
22690
22731
22733
22734
22738
22739
22759
22779
22834
22835
22844
22845
22865
22866
22867
22892
22904
22906
22940
22941
2

23171
23173
23175
23243
23245
23252
23298
23397
23401
23404
23408
23432
23444
47566
47566B
48138
48187
79321
82484
84380
84879
85059
85066
6
1
84968A
6
21731
22418
22449
22451
22617
22837
10
21316
21320
22791
22980
23041
23042
23045
23145
84968C
84978
79
18097C
20751
20752
20754
20914
20956
21218
21394
21395
21398
21399
21422
21563
21669
21671
21673
21977
22065
22075
22076
22094
22203
22204
22554
22557
22666
22667
22720
22722
22809
22810
22907
22960
22961
22963
22966
22969
22978
22979
22980
23080
23113
23154
23166
23167
23236
23240
23243
23251
23293
23294
23295
23297
23298
23299
23306
23307
23318
23319
23324
23326
23358
23359
23382
23493
23495
23503
23534
23538
23541
71459
72799E
84375
84378
84380
84997A
84997B
84997C
85230B
6
1
79302M
8
21108
21231
21974
22720
22851
22989
84509A
84988
9
20972
22568
22865
23076
23085
23241
23348
23434
84946
7
15056P
20679
20724
22465
23099
23323
84879
6
20914
22111
22114
22595
22727
23301
10
22084
22180
22358
22467
22495
22499
22611
22725
22727
82484
6

In [111]:
len(user_profiles)

4335

In [112]:
print(user_profiles)

{12346: <1x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 8 stored elements in Compressed Sparse Row format>, 12347: <103x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 593 stored elements in Compressed Sparse Row format>, 12348: <20x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 133 stored elements in Compressed Sparse Row format>, 12349: <72x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 436 stored elements in Compressed Sparse Row format>, 12350: <16x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 82 stored elements in Compressed Sparse Row format>, 12352: <57x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 326 stored elements in Compressed Sparse Row format>, 12353: <4x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 31 stored elements in Compressed Sparse Row format>, 12354: <57x3033 sparse matrix of type '<class 'numpy.float64'>'
	with 338 stored elements in Compressed Sparse Row format>, 12355: <12x3

In [113]:
print(len(purchases_full_indexed_df.index.unique()))

4335


In [114]:
#Creating the mxn matrix
users = purchases_full_indexed_df.index.unique()
result = []
count=0
len(users)
for user_id in users:
    print("working on user #{}".format(user_id))
    user_product_similarity = cosine_similarity(user_profiles[user_id],tfidf_matrix)
    user_product_similarity = user_product_similarity.mean(axis=0)
    if count == 0:
        result = scipy.sparse.coo_matrix(user_product_similarity)
    else:
        result = scipy.sparse.vstack((result,user_product_similarity))
    count += 1

working on user #12346
working on user #12347
working on user #12348
working on user #12349
working on user #12350
working on user #12352
working on user #12353
working on user #12354
working on user #12355
working on user #12356
working on user #12357
working on user #12358
working on user #12359
working on user #12360
working on user #12361
working on user #12362
working on user #12363
working on user #12364
working on user #12365
working on user #12367
working on user #12370
working on user #12371
working on user #12372
working on user #12373
working on user #12374
working on user #12375
working on user #12377
working on user #12378
working on user #12379
working on user #12380
working on user #12381
working on user #12383
working on user #12384
working on user #12386
working on user #12388
working on user #12390
working on user #12391
working on user #12393
working on user #12394
working on user #12395
working on user #12397
working on user #12398
working on user #12399
working on 

working on user #12793
working on user #12794
working on user #12795
working on user #12797
working on user #12798
working on user #12802
working on user #12808
working on user #12809
working on user #12811
working on user #12812
working on user #12814
working on user #12815
working on user #12816
working on user #12817
working on user #12818
working on user #12820
working on user #12821
working on user #12822
working on user #12823
working on user #12824
working on user #12826
working on user #12827
working on user #12828
working on user #12829
working on user #12830
working on user #12831
working on user #12832
working on user #12833
working on user #12834
working on user #12836
working on user #12837
working on user #12838
working on user #12839
working on user #12840
working on user #12841
working on user #12842
working on user #12843
working on user #12844
working on user #12845
working on user #12847
working on user #12849
working on user #12851
working on user #12852
working on 

working on user #13296
working on user #13297
working on user #13298
working on user #13299
working on user #13300
working on user #13301
working on user #13302
working on user #13304
working on user #13305
working on user #13307
working on user #13308
working on user #13309
working on user #13310
working on user #13311
working on user #13313
working on user #13314
working on user #13316
working on user #13317
working on user #13318
working on user #13319
working on user #13320
working on user #13321
working on user #13322
working on user #13323
working on user #13324
working on user #13325
working on user #13327
working on user #13328
working on user #13329
working on user #13330
working on user #13332
working on user #13334
working on user #13336
working on user #13338
working on user #13339
working on user #13340
working on user #13341
working on user #13343
working on user #13344
working on user #13345
working on user #13347
working on user #13348
working on user #13349
working on 

working on user #13801
working on user #13802
working on user #13803
working on user #13804
working on user #13805
working on user #13806
working on user #13807
working on user #13808
working on user #13809
working on user #13810
working on user #13811
working on user #13812
working on user #13813
working on user #13814
working on user #13815
working on user #13816
working on user #13817
working on user #13819
working on user #13821
working on user #13822
working on user #13823
working on user #13824
working on user #13826
working on user #13827
working on user #13828
working on user #13831
working on user #13832
working on user #13833
working on user #13835
working on user #13837
working on user #13838
working on user #13841
working on user #13842
working on user #13844
working on user #13845
working on user #13846
working on user #13848
working on user #13849
working on user #13850
working on user #13851
working on user #13853
working on user #13854
working on user #13856
working on 

working on user #14293
working on user #14295
working on user #14297
working on user #14298
working on user #14299
working on user #14300
working on user #14301
working on user #14304
working on user #14305
working on user #14306
working on user #14307
working on user #14309
working on user #14311
working on user #14312
working on user #14314
working on user #14315
working on user #14317
working on user #14320
working on user #14321
working on user #14323
working on user #14326
working on user #14327
working on user #14329
working on user #14331
working on user #14332
working on user #14333
working on user #14334
working on user #14335
working on user #14336
working on user #14338
working on user #14339
working on user #14340
working on user #14341
working on user #14342
working on user #14344
working on user #14345
working on user #14346
working on user #14348
working on user #14349
working on user #14350
working on user #14351
working on user #14352
working on user #14353
working on 

...

working on user #16243
working on user #16244
working on user #16245
working on user #16247
working on user #16248
working on user #16249
working on user #16250
working on user #16253
working on user #16255
working on user #16256
working on user #16257
working on user #16258
working on user #16260
working on user #16261
working on user #16265
working on user #16266
working on user #16268
working on user #16270
working on user #16271
working on user #16272
working on user #16274
working on user #16275
working on user #16276
working on user #16278
working on user #16279
working on user #16281
working on user #16282
working on user #16283
working on user #16284
working on user #16287
working on user #16292
working on user #16293
working on user #16295
working on user #16297
working on user #16298
working on user #16302
working on user #16303
working on user #16305
working on user #16306
working on user #16308
working on user #16309
working on user #16311
working on user #16313
working on 

working on user #16744
working on user #16745
working on user #16746
working on user #16747
working on user #16748
working on user #16750
working on user #16751
working on user #16752
working on user #16753
working on user #16754
working on user #16755
working on user #16756
working on user #16757
working on user #16758
working on user #16759
working on user #16761
working on user #16762
working on user #16763
working on user #16764
working on user #16765
working on user #16766
working on user #16767
working on user #16768
working on user #16769
working on user #16770
working on user #16771
working on user #16773
working on user #16774
working on user #16775
working on user #16776
working on user #16777
working on user #16778
working on user #16779
working on user #16780
working on user #16781
working on user #16782
working on user #16784
working on user #16788
working on user #16789
working on user #16790
working on user #16791
working on user #16792
working on user #16793
working on 

working on user #17238
working on user #17239
working on user #17242
working on user #17243
working on user #17244
working on user #17245
working on user #17247
working on user #17248
working on user #17250
working on user #17251
working on user #17252
working on user #17253
working on user #17254
working on user #17255
working on user #17256
working on user #17259
working on user #17262
working on user #17263
working on user #17265
working on user #17266
working on user #17267
working on user #17268
working on user #17272
working on user #17274
working on user #17277
working on user #17278
working on user #17279
working on user #17282
working on user #17284
working on user #17286
working on user #17287
working on user #17288
working on user #17289
working on user #17290
working on user #17291
working on user #17293
working on user #17295
working on user #17297
working on user #17298
working on user #17299
working on user #17301
working on user #17302
working on user #17303
working on 

working on user #17727
working on user #17728
working on user #17730
working on user #17731
working on user #17732
working on user #17733
working on user #17734
working on user #17735
working on user #17736
working on user #17737
working on user #17738
working on user #17739
working on user #17742
working on user #17744
working on user #17746
working on user #17747
working on user #17749
working on user #17750
working on user #17752
working on user #17754
working on user #17757
working on user #17758
working on user #17759
working on user #17760
working on user #17761
working on user #17763
working on user #17764
working on user #17765
working on user #17767
working on user #17768
working on user #17769
working on user #17770
working on user #17771
working on user #17772
working on user #17774
working on user #17775
working on user #17777
working on user #17779
working on user #17781
working on user #17783
working on user #17785
working on user #17786
working on user #17787
working on 

working on user #18225
working on user #18226
working on user #18227
working on user #18228
working on user #18229
working on user #18230
working on user #18231
working on user #18232
working on user #18233
working on user #18235
working on user #18236
working on user #18237
working on user #18239
working on user #18240
working on user #18241
working on user #18242
working on user #18245
working on user #18246
working on user #18248
working on user #18249
working on user #18250
working on user #18251
working on user #18252
working on user #18255
working on user #18257
working on user #18259
working on user #18260
working on user #18261
working on user #18262
working on user #18263
working on user #18265
working on user #18268
working on user #18269
working on user #18270
working on user #18272
working on user #18273
working on user #18274
working on user #18276
working on user #18277
working on user #18278
working on user #18280
working on user #18281
working on user #18282
working on 

In [115]:
result.shape

(4335, 3659)

In [116]:
content_based_result = result.todense()
content_based_result.shape

(4335, 3659)

In [117]:
content = np.array(content_based_result)
content

array([[0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.01260941, 0.00465927, 0.00575894, ..., 0.        , 0.00425312,
        0.        ],
       [0.00248883, 0.        , 0.00608386, ..., 0.        , 0.03263945,
        0.00916767],
       ...,
       [0.        , 0.        , 0.00343376, ..., 0.        , 0.00524149,
        0.01031749],
       [0.01067502, 0.00712775, 0.01053302, ..., 0.        , 0.00550566,
        0.00284622],
       [0.01065398, 0.00399316, 0.04992605, ..., 0.        , 0.0046747 ,
        0.        ]])

In [201]:
np.savetxt("content_filter.csv", content, delimiter=",")

## 4. Collaborative Filtering

There are many model-based CF algorithms to recommend items to users such as neural networks, bayerian networks, clustering models, and latent factor models such as Singular Value Decomposition (SVD) and, probabilistic latent semantic analysis. 

### Matrix Factorization: SVD

Latent factor models compress the user-item matrix into a low-dimensional representation in terms of latent factors. One advantage of using this approach is that instead of having a high dimensional matrix containing a large number of missing values, we will be dealing with a much smaller matrix in lower-dimensional space. 

We will be using a popular latent factor model named Singular Value Decomposition (SVD). There are other frameworks such as surprise, mrec, python-recsys that are specific to Collaborative Filters, however, we'll stick with SciPy.

In [118]:
Purchases_df = prop.groupby(['customer_id','product_id'])['value'].mean().reset_index()
print('# of unique customer/item purchases: %d' % len(Purchases_df))
Purchases_df.describe()

# of unique customer/item purchases: 212995


customer_id          value
count  212995.000000  212995.000000
mean    15273.910899       3.490932
std      1710.864276       1.345601
min     12346.000000       0.000000
25%     13862.000000       2.572890
50%     15214.000000       3.666757
75%     16771.000000       4.238515
max     18287.000000      17.362137

In [119]:
#Creating a sparse pivot table with users in rows and items in columns
users_items_pivot_matrix_df = Purchases_df.pivot(index='customer_id',
                                                      columns='product_id',
                                                      values='value').fillna(0)
users_items_pivot_matrix_df.head(100)

product_id      10002  10080  10120  10123C  10124A  10124G  10125  10133  \
customer_id                                                                 
12346        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12347        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12348        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12349        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12350        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12352        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12353        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12354        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12355        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12356        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12357        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12358        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12359        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12360        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12361        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12362        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12363        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12364        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12365        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12367        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12370        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12371        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12372        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12373        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12374        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12375        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12377        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12378        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12379        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12380        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
...               ...    ...    ...     ...     ...     ...    ...    ...   
12432        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12433        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12434        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12435        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12436        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12437        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12438        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12441        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12442        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12444        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12445        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12446        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12447        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12448        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12449        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12450        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12451        3.485427    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12452        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0   
12453        0.000000    0.0    0.0     0.0     0.0     0.0    0.0    0.0

In [ ]:
Purchases_training_df = training_purchases.groupby(['customer_id','product_id'])['value'].mean().reset_index()
print('# of unique customer/item purchases: %d' % len(Purchases_df))
Purchases_df.describe()

In [ ]:
Purchases_testing_df = testing_purchases.groupby(['customer_id','product_id'])['value'].mean().reset_index()
print('# of unique customer/item purchases: %d' % len(Purchases_df))
Purchases_df.describe()

In [ ]:
#Creating a sparse pivot table with users in rows and items in columns

training_data_matrix_df = Purchases_training_df.pivot(index='customer_id',
                                                      columns='product_id',
                                                      values='value').fillna(0)
training_data_matrix_df.head(100)

In [ ]:
#Creating a sparse pivot table with users in rows and items in columns

test_data_matrix = Purchases_testing_df.pivot(index='customer_id',
                                                      columns='product_id',
                                                      values='value').fillna(0)
test_data_matrix.head(100)

In [120]:
users_items_pivot_matrix = users_items_pivot_matrix_df.as_matrix()
users_items_pivot_matrix[:10]

C:\Users\Prakash14\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  """Entry point for launching an IPython kernel.


array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [121]:
users_ids = list(users_items_pivot_matrix_df.index)
users_ids[:10]

[12346, 12347, 12348, 12349, 12350, 12352, 12353, 12354, 12355, 12356]

The number of matrix factors determines the number of features our model learns. The greater the number of features the better trained the model. However, it may then be prone to overfitting and a poor predictor of future events. 

In [122]:
matrix_factors = 25 
U, sigma, Vt = svds(users_items_pivot_matrix, k = matrix_factors)

In [123]:
U.shape

(4335, 25)

In [124]:
Vt.shape

(25, 3659)

In [125]:
sigma = np.diag(sigma)
sigma.shape

(25, 25)

In [126]:
all_user_predicted_ratings = np.dot(np.dot(U,sigma),Vt)
all_user_predicted_ratings

array([[-3.70558019e-03, -1.03015154e-03, -2.38293529e-03, ...,
        -1.40780105e-04, -4.86241307e-04, -1.40780105e-04],
       [ 2.48415709e-01,  2.12308867e-02,  5.85376700e-04, ...,
        -5.65316961e-04,  6.43530954e-04, -5.65316961e-04],
       [ 7.59002445e-02,  2.62104186e-02, -2.24299571e-03, ...,
        -8.00312657e-04, -1.46787514e-03, -8.00312657e-04],
       ...,
       [-1.82251429e-02,  2.86983068e-03, -3.68632470e-03, ...,
         1.84802230e-04,  3.26459890e-04,  1.84802230e-04],
       [ 6.57446728e-02,  2.61669562e-02,  1.38986274e-02, ...,
         1.22756812e-03, -3.42228346e-03,  1.22756812e-03],
       [ 8.14278301e-02,  2.62140896e-02,  1.58985644e-02, ...,
         2.29873731e-04,  5.82396648e-03,  2.29873731e-04]])

In [127]:
all_user_predicted_ratings.shape

(4335, 3659)

In [129]:
cf_preds_df = pd.DataFrame(all_user_predicted_ratings, 
                           columns = users_items_pivot_matrix_df.columns,
                           index=users_ids).transpose()
cf_preds_df.head(100)

12346     12347     12348     12349         12350     12352  \
product_id                                                                   
10002      -0.003706  0.248416  0.075900  0.038143  3.541200e-02  0.006237   
10080      -0.001030  0.021231  0.026210 -0.015078  2.852887e-03  0.005727   
10120      -0.002383  0.000585 -0.002243 -0.006717  2.924232e-03 -0.007262   
10123C     -0.000225 -0.000057  0.000760  0.000020  6.379148e-05 -0.001070   
10124A      0.000032  0.002136  0.001222  0.006878  6.502103e-04  0.002500   
10124G     -0.000322 -0.003766  0.003009  0.002609 -2.803317e-04 -0.001859   
10125      -0.009660 -0.006956  0.066957  0.101155  8.988848e-03  0.040598   
10133       0.019089  0.156726  0.039679  0.124704  3.136106e-02  0.167150   
10135      -0.013649  0.096286  0.108352  0.056199  6.394124e-02  0.076052   
11001      -0.006302  0.104625 -0.009995  0.052594  4.574124e-02 -0.011179   
15030      -0.000169  0.004976  0.003016  0.007072  1.409617e-03  0.001622   
15034      -0.007111  0.140082  0.196780 -0.010500  1.857734e-02  0.034779   
15036       0.056686  1.021377  0.674418  0.042782  2.235604e-01  0.119235   
15039      -0.007062  0.203185  0.221454 -0.084894  8.214452e-03 -0.027531   
15044A      0.011296  0.152580  0.132784  0.005340  2.237476e-02  0.079816   
15044B     -0.008159  0.114873  0.139778 -0.048190  1.506648e-02 -0.023628   
15044C     -0.001851  0.099454  0.205276 -0.067628  1.431228e-02 -0.000774   
15044D      0.005828  0.190331  0.240693 -0.083603  2.576296e-02 -0.083739   
15056BL    -0.007527  0.274608 -0.115285  0.655382  5.192126e-02  0.453368   
15056N      0.021373  0.641610  0.193713  0.298475  1.680103e-02  0.379863   
15056P      0.011941  0.232968  0.133533  0.187389  3.880649e-02  0.112068   
15058A     -0.001876 -0.019248 -0.076414  0.184663 -1.920390e-02  0.204654   
15058B      0.005669 -0.040410 -0.036853  0.139853 -1.799342e-02  0.075545   
15058C     -0.019404  0.018566  0.095370  0.092655 -9.557885e-03 -0.122736   
15060B     -0.011209  0.126842  0.028334  0.155076 -3.742751e-02  0.233449   
16008       0.000715  0.188452  0.035477  0.060076  2.652316e-03  0.079238   
16010      -0.000439  0.004456  0.000290  0.002947  8.938496e-04  0.002172   
16011      -0.002427  0.080705  0.025357  0.001520  1.014583e-02 -0.019648   
16012      -0.005089  0.052686  0.043815 -0.014022  1.699025e-02  0.012161   
16014       0.014471  0.088811  0.003804  0.018451  1.629664e-02 -0.027694   
...              ...       ...       ...       ...           ...       ...   
16244B      0.000432 -0.002369  0.004471  0.007362  8.626448e-04  0.002313   
16248B     -0.000513  0.002565  0.001188 -0.008026 -6.160679e-05  0.000687   
16254      -0.000961 -0.003431  0.001659  0.009383  6.512621e-04  0.003379   
16258A     -0.009480  0.034759  0.005037  0.002244  2.013056e-02  0.025301   
16259       0.006379  0.054765 -0.000720 -0.020925 -4.744509e-03 -0.059502   
17001      -0.000040  0.000273  0.000319  0.000130  8.600906e-07  0.000093   
17003      -0.016276  0.098435  0.075785 -0.067047  5.746468e-02  0.033030   
17007B     -0.000286 -0.001106 -0.002100  0.006776 -1.697858e-03 -0.001596   
17011F      0.000165  0.024316 -0.003619  0.000057  4.311180e-03  0.015026   
17012A      0.014931  0.083319  0.006066  0.058531  2.033463e-02  0.003710   
17012B      0.012310  0.142541  0.007760  0.026770  2.664046e-02  0.002077   
17012C     -0.001604  0.031539 -0.015131  0.013574  6.465017e-03  0.024680   
17012D      0.025663  0.109821  0.019909  0.063865  2.986872e-02 -0.015108   
17012E      0.010718  0.066110 -0.020189  0.002203  4.035166e-03 -0.054532   
17012F      0.011038  0.119126 -0.023990 -0.016667  7.782922e-03 -0.073828   
17013D      0.002509  0.140119  0.024421  0.071063 -1.654037e-02  0.086259   
17014A     -0.000150  0.000611  0.003951 -0.002712  2.864491e-03  0.003202   
17021      -0.005330  0.176864  0.046212 -0.008202  2.392487e-03  0.041988   
17028J     -0.000055  0.000347  0.000

In [130]:
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import label_binarize
#users_items_pivot_matrix = label_binarize(users_items_pivot_matrix, classes=[0, 1])
#all_user_predicted_ratings = label_binarize(all_user_predicted_ratings,classes=[0,1])
print (mean_squared_error(users_items_pivot_matrix,all_user_predicted_ratings))

0.1465715228416058


In [131]:
print (mean_squared_error(users_items_pivot_matrix,content_based_result))

0.1876157439998291


We can see that mean squared error wise the collaborative filter actually performs better than the content based filter, as can be expected for most cases in our dataset

In [139]:
np.savetxt("collab_filter.csv", all_user_predicted_ratings, delimiter=",")

## 5. Hybrid content based and collaborative recommendation

We can just smash the two matrix together by mutliplying them. However, we know that content based reccommdations are better equiped to overcome the cold start problem. So one method we could undertake is to weight the content based filter to have heavier implications for users that have bought less than 5 unique purchases. 

In [136]:
hybrid = np.multiply(all_user_predicted_ratings,content)

In [137]:
hybrid.shape

(4335, 3659)

In [138]:
print (mean_squared_error(users_items_pivot_matrix,hybrid))

0.18738725191146646


**HULK SMASH** doesn't work because most of the elements are zero for the content based matrix

In [ ]:
all_user_predicted_ratings

In [ ]:
content

In [186]:
user_purchases = prop.groupby('customer_id')['quantity'].size().sort_values(ascending=False).reset_index()

In [134]:
users_low_purchases = user_purchases[user_purchases.quantity<5]
users_low_purchases.describe()

customer_id    quantity
count    291.000000  291.000000
mean   15380.144330    2.419244
std     1734.977313    1.148991
min    12346.000000    1.000000
25%    13947.500000    1.000000
50%    15316.000000    2.000000
75%    16820.000000    3.000000
max    18273.000000    4.000000

291 users with purchases less than 5. These can be great candidates for content based recommendations

In [140]:
users_low_purchases.head()

customer_id  quantity
4044        18246         4
4045        17900         4
4046        12401         4
4047        12403         4
4048        17844         4

In [141]:
check = cf_preds_df.transpose()
check

product_id     10002     10080     10120    10123C    10124A        10124G  \
12346      -0.003706 -0.001030 -0.002383 -0.000225  0.000032 -3.219491e-04   
12347       0.248416  0.021231  0.000585 -0.000057  0.002136 -3.765909e-03   
12348       0.075900  0.026210 -0.002243  0.000760  0.001222  3.009289e-03   
12349       0.038143 -0.015078 -0.006717  0.000020  0.006878  2.608617e-03   
12350       0.035412  0.002853  0.002924  0.000064  0.000650 -2.803317e-04   
12352       0.006237  0.005727 -0.007262 -0.001070  0.002500 -1.858538e-03   
12353      -0.000382  0.001574  0.000200  0.000152  0.000167  4.447555e-04   
12354       0.090603 -0.019317 -0.007311  0.001413  0.002814  4.407482e-03   
12355       0.017990  0.014661 -0.000643 -0.000072  0.001815 -1.623397e-03   
12356       0.114171  0.004056 -0.010318  0.001961  0.001278  3.788302e-03   
12357       0.112678  0.019776  0.020959  0.000605  0.016460  2.859999e-03   
12358       0.054337  0.014208  0.000341 -0.000225  0.000030 -1.563652e-03   
12359       0.061079 -0.051038  0.026610 -0.005171 -0.001148 -7.122523e-03   
12360       0.171730 -0.014257  0.020279  0.000732  0.004578  1.086471e-02   
12361       0.080588  0.001082 -0.004453 -0.000039  0.002813  1.141608e-04   
12362       0.438225  0.027440  0.001005 -0.004240  0.009875 -7.319146e-03   
12363       0.056005 -0.006211 -0.018278  0.001196 -0.001051  1.463042e-03   
12364       0.144283  0.013697 -0.014581  0.002831 -0.001377  3.290169e-03   
12365       0.001027  0.004336 -0.005881  0.000174 -0.000634 -1.110695e-03   
12367       0.046633  0.006731 -0.000709 -0.000147  0.000872 -8.590981e-04   
12370       0.083248  0.023986  0.047714  0.006763 -0.001617  7.381822e-03   
12371       0.059593 -0.001803  0.022980 -0.000264  0.012599  1.288016e-04   
12372       0.138994  0.005735  0.003909 -0.000548  0.002216 -2.383122e-03   
12373       0.052555 -0.000889 -0.002602 -0.000354 -0.000050 -1.144112e-03   
12374       0.014302  0.011336 -0.000771 -0.000321  0.004119 -4.712266e-04   
12375       0.026825 -0.002461  0.003795 -0.000284 -0.001064 -5.142612e-05   
12377       0.238624 -0.018779  0.020774  0.001137  0.006092  2.541777e-04   
12378       0.412096 -0.007016 -0.000486  0.003921  0.005830  1.640536e-02   
12379       0.164000 -0.015614 -0.000625  0.000908  0.006059  4.852350e-03   
12380       0.126752 -0.015292 -0.005582  0.001206  0.001703  6.778237e-03   
...              ...       ...       ...       ...       ...           ...   
18242      -0.006469  0.020900 -0.030241 -0.002358 -0.000051 -1.154887e-02   
18245       0.030526  0.028940 -0.003840  0.001585  0.001340 -4.960889e-03   
18246       0.015315  0.001569 -0.000119  0.000099 -0.000719 -9.349160e-04   
18248       0.016770 -0.002837 -0.005753  0.001606 -0.002063 -3.193033e-03   
18249       0.021368  0.005664  0.004445 -0.000025  0.000395  1.548199e-05   
18250      -0.063687 -0.011470 -0.003535 -0.000236  0.002951  4.920064e-03   
18251       0.046396  0.005361 -0.024358  0.001162 -0.001395  1.577038e-03   
18252       0.013966  0.011742 -0.001809 -0.000783 -0.000773 -3.993519e-03   
18255       0.000680  0.001331 -0.000143  0.000136 -0.000069  1.494636e-04   
18257      -0.027655  0.005086  0.008554 -0.001528  0.004420  4.332840e-03   
18259      -0.046544 -0.022003  0.012016 -0.000537  0.007155 -2.439086e-03   
18260       0.087145  0.019759 -0.024727  0.003792 -0.002057 -4.699033e-03   
18261      -0.020267 -0.009978  0.013017  0.000304 -0.001745  4.390167e-03   
18262      -0.002714 -0.003206 -0.002750  0.000406  0.000923  3.109989e-03   
18263       0.042665  0.021102  0.023227 -0.000309  0.001179  8.941339e-04   
18265       0.041374  0.009552 -0.017843 -0.001467 -0.001189 -8.150810e-03   
18268       0.003395  0.000027 -0.000178  0.000007 -0.000093 -1.352806e-04   
18269       0.022480  0.004273  0.002256 -0.000153  0.000423 -3.061909e-04   
18270      -0.003770  0.000805  0.002642  0.000156 -0.000011  8.540577e-04   
18272      -0.109978 -

In [142]:
check.index.values

array([12346, 12347, 12348, ..., 18282, 18283, 18287], dtype=int64)

In [143]:
hybrid_matrix = all_user_predicted_ratings
row_number = 0
count = 0
for i in check.index.values:
    for customer_id in users_low_purchases['customer_id']:
        if i == customer_id:
            hybrid_matrix[row_number] = content_based_result[row_number]
            count +=1
            print(hybrid_matrix[row_number])
    row_number += 1

[0. 0. 0. ... 0. 0. 0.]
[0.05385289 0.         0.         ... 0.0975574  0.         0.        ]
[0.        0.        0.        ... 0.0390523 0.        0.       ]
[0.         0.03701079 0.03056005 ... 0.         0.01066636 0.        ]
[0.01837574 0.02601901 0.         ... 0.         0.         0.        ]
[0.0165922  0.         0.03983578 ... 0.         0.01410134 0.06141489]
[0.         0.         0.         ... 0.         0.01668215 0.        ]
[0. 0. 0. ... 0. 0. 0.]
[0.         0.02616608 0.02281794 ... 0.         0.         0.        ]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0.01689179 0.06827778 0.         ... 0.         0.01175124 0.        ]
[0.03378357 0.04783563 0.         ... 0.         0.         0.        ]
[0.         0.         0.05402647 ... 0.         0.         0.        ]
[0.        0.        0.        ... 0.        0.0104812 0.       ]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0.09365081 0.         0.         ... 0.         0.         0.        ]
[0. 

[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0.         0.         0.01816562 ... 0.         0.09255158 0.        ]
[0.09828631 0.         0.         ... 0.         0.04627579 0.        ]
[0. 0. 0. ... 0. 0. 0.]
[0.07737451 0.10955794 0.         ... 0.         0.         0.        ]
[0. 0. 0. ... 0. 0. 0.]
[0.         0.         0.07486827 ... 0.         0.         0.        ]
[0. 0. 0. ... 0. 0. 0.]
[0. 0. 0. ... 0. 0. 0.]
[0.08958683 0.         0.         ... 0.         0.         0.        ]
[0.         0.         0.         ... 0.06345753 0.         0.        ]
[0.         0.         0.02141576 ... 0.         0.02049714 0.        ]
[0.01528019 0.         0.         ... 0.         0.         0.        ]
[0.         0.14804318 0.         ... 0.         0.         0.        ]
[0.         0.         0.         ... 0.         0.         0.33333333]
[0.        0.        0.        ... 0.        0.0937688 0.       

In [144]:
print(count)

291


In [145]:
hybrid_matrix.shape

(4335, 3659)

In [146]:
print (mean_squared_error(users_items_pivot_matrix,hybrid_matrix))

0.1467509486682655


In [198]:
np.savetxt("hybrid_filter.csv", hybrid_matrix, delimiter=",")

## Conclusion

There is large room for improvements of the results. 

Firstly, I would have loved to tune the hyperparameters for both models with a cross validation set. With time considerations, I've just gone with best practices. 

Also, we've completely ignored the time, we could further leverage the available contextual information to model users preferences across time (period of day, day of week, month) and country.
This contextual information can be easily incorporated in Learn-to-Rank models (like XGBoost Gradient Boosting Decision Trees with ranking objective) or Logistic models (with categorical features One-Hot encoded or Feature Hashed). 

There are more advanced techniques in RecSys research community that could be worth exploring, specially advanced Matrix Factorization and Deep Learning models.